<a href="https://colab.research.google.com/github/LucasOsco/RemoteSensingAI/blob/main/GeospatialSAM_MultipleBbox_vLinkedIn.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

***Connect to Drive***

In [1]:
from google.colab import drive 
drive.mount('/content/gdrive')

Mounted at /content/gdrive


***Install dependencies***

In [2]:
pip install segment-geospatial leafmap localtileserver

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 76.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19.4/19.4 MB 54.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.2/40.2 kB 6.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.6/14.6 MB 95.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 81.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.0/20.0 MB 63.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 55.4/55.4 kB 8.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.0/5.0 MB 92.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 85.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 96.5/96.5 kB 14.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 130.5/130.5 kB 19.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━

In [3]:
pip install pycrs

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Preparing metadata (setup.py) ... done
  Created wheel for pycrs: filename=PyCRS-1.0.2-py3-none-any.whl size=32686 sha256=072bf704d131dd5d4ac777e811c1aef0e5e653d3d97948c44842c668cc477782
  Stored in directory: /root/.cache/pip/wheels/47/1d/70/7a5bdf33347e7c75e95b06b1fa38f076a59a9506653cc24aff
Successfully built pycrs


***Import libraries***

In [4]:
import os
import leafmap
import torch
import cv2
import geopandas as gpd
from samgeo import SamGeo, SamGeoPredictor, tms_to_geotiff, get_basemaps
from segment_anything import sam_model_registry
from pathlib import Path

***Load image and shapefile from Drive***

In [5]:
# Read the image
image = 'gdrive/My Drive/Colab Notebooks/Image/roi_image.tif'

# Read the shapefile
shapefile = 'gdrive/My Drive/Colab Notebooks/Shape/roi_bbox.shp'
gdf = gpd.read_file(shapefile)

# Extract bounding boxes from the shapefile
clip_boxes = [list(geom.bounds) for geom in gdf.geometry]

***Create an interactive map***

In [6]:
zoom = 19
style_bbox = {'color': '#FFFF00', 'weight': 1, 'fillColor': '#FFFF00', 'fillOpacity': 0.3,}
style_segmented = {'color': '#a37aa9', 'weight': 1, 'fillColor': '#a37aa9', 'fillOpacity': 0.9,}

m = leafmap.Map(center=[-22.17615, -51.253043], zoom=zoom)

m.add_raster(image, layer_name='Image')
m.add_vector(shapefile, layer_name='Vector', style=style_bbox)
m

Map(center=[-22.17615, -51.253043], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title'…

***Initialize SamGeoPredictor class***

In [7]:
# Load the model from Drive
out_dir = os.path.join('gdrive/My Drive/Colab Notebooks/Model/')
checkpoint = os.path.join(out_dir, 'sam_vit_h_4b8939.pth')

In [8]:
img_arr = cv2.imread(image)

model_type = "vit_h"

sam = sam_model_registry[model_type](checkpoint=checkpoint)

predictor = SamGeoPredictor(sam)

predictor.set_image(img_arr)

***Combine the segmentations and load the results on the map***

In [9]:
combined_gdf = gpd.GeoDataFrame()

# Process each clip_box
for i, clip_box in enumerate(clip_boxes):
    masks, _, _ = predictor.predict(src_fp=image, geo_box=clip_box)

    masks_img = f"preds_{i}.tif"
    predictor.masks_to_geotiff(image, masks_img, masks.astype("uint8"))

    vector = f"feats_{i}.geojson"
    temp_gdf = predictor.geotiff_to_geojson(masks_img, vector, bidx=1)
    combined_gdf = combined_gdf.append(temp_gdf)
    combined_gdf.set_geometry('geometry', inplace=True)

    m.add_vector(vector, layer_name=f'Vector_{i}', style=style_segmented)

***Export the shapefile to Drive***

In [10]:
# Set the CRS for the combined GeoDataFrame (use the same CRS as your input shapefile)
combined_gdf.crs = 'EPSG:4326'

# Save the combined GeoDataFrame as a Shapefile
output_shapefile = 'gdrive/My Drive/Colab Notebooks/Output/roi_segmented.shp'
combined_gdf.to_file(output_shapefile)